In [2]:
import pickle
with open('message_failed_tokens.pickle', 'rb') as f:
    failed = pickle.load(f)
with open('message_success_tokens.pickle', 'rb') as f:
    success = pickle.load(f)

In [11]:
type(messages)

list

In [3]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(2018)
import nltk
nltk.download('wordnet')
#nlp = en_core_web_md.load()
from spacy.lang.en import English
parser = English()


[nltk_data] Downloading package wordnet to /home/anant/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [4]:
dictionary = gensim.corpora.Dictionary(failed + success)
count = 0
for k, v in dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break

0 august
1 coleen
2 coleen@mascherino.com
3 email
4 file
5 flyerclick
6 group
7 hello
8 mascherino
9 promotion
10 regard


In [5]:
dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)

In [7]:
all = failed + success

In [8]:
bow_corpus_fail = [dictionary.doc2bow(doc) for doc in failed]
bow_corpus_success = [dictionary.doc2bow(doc) for doc in success]

In [11]:
from gensim import corpora, models
tfidf_fail = models.TfidfModel(bow_corpus_fail)
tfidf_success = models.TfidfModel(bow_corpus_success)
corpus_tfidf_fail = tfidf_fail[bow_corpus_fail]
corpus_tfidf_success = tfidf_success[bow_corpus_success]
from pprint import pprint
for doc in corpus_tfidf_success:
    pprint(doc)
    break

[(4, 0.14299089127458958),
 (10, 0.0662945448954322),
 (11, 0.07113887140189622),
 (33, 0.08842923132042707),
 (54, 0.1574283021319686),
 (105, 0.08730130536047566),
 (150, 0.10879307056580513),
 (561, 0.20790058095521383),
 (1544, 0.36950521920613605),
 (1862, 0.2627184766172895),
 (1864, 0.3124463824144368),
 (1867, 0.3553325763171855),
 (3955, 0.28011158180639373),
 (5613, 0.3618630001600954),
 (5934, 0.3485727409697511),
 (7552, 0.3383268047495328)]


In [12]:
lda_model_fail = gensim.models.LdaMulticore(bow_corpus_fail, num_topics=10, id2word=dictionary, passes=2, workers=2)
lda_model_success = gensim.models.LdaMulticore(bow_corpus_success, num_topics=10, id2word=dictionary, passes=2, workers=2)

In [13]:
for idx, topic in lda_model_success.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

Topic: 0 
Words: 0.048*"company" + 0.035*"associate" + 0.033*"excite" + 0.029*"saturday" + 0.025*"every" + 0.024*"april" + 0.021*"idlife" + 0.019*"bonus" + 0.018*"would" + 0.018*"great"
Topic: 1 
Words: 0.050*"better" + 0.037*"idlife" + 0.037*"wellness" + 0.031*"health" + 0.030*"morning" + 0.030*"idtransformation" + 0.030*"replace" + 0.020*"learn" + 0.019*"appetite" + 0.019*"answer"
Topic: 2 
Words: 0.073*"photo" + 0.042*"email" + 0.041*"match" + 0.036*"mutual" + 0.033*"wherein" + 0.025*"receive" + 0.014*"caraway" + 0.014*"gloria" + 0.013*"average" + 0.012*"682.365.3032"
Topic: 3 
Words: 0.072*"file" + 0.039*"regard" + 0.036*"suggest" + 0.032*"idlife" + 0.029*"video" + 0.015*"product" + 0.014*"dettmer" + 0.014*"jdettmer@hotmail.com" + 0.012*"please" + 0.012*"thanks"
Topic: 4 
Words: 0.095*"period" + 0.094*"revealing" + 0.048*"phase" + 0.028*"sleep" + 0.018*"increase" + 0.018*"1,000" + 0.014*"click" + 0.012*"investing" + 0.012*"help" + 0.011*"visit"
Topic: 5 
Words: 0.216*".coupon" + 0.

In [14]:
lda_model_tfidf_fail = gensim.models.LdaMulticore(corpus_tfidf_fail, num_topics=10, id2word=dictionary, passes=2, workers=4)
lda_model_tfidf_success = gensim.models.LdaMulticore(corpus_tfidf_success, num_topics=10, id2word=dictionary, passes=2, workers=4)
for idx, topic in lda_model_tfidf_fail.print_topics(-1):
    print('Topic: {} Word: {}'.format(idx, topic))

Topic: 0 Word: 0.031*"saturday" + 0.025*"april" + 0.021*"aikman" + 0.020*"dallas" + 0.017*"partner" + 0.017*"company" + 0.016*"associate" + 0.016*"every" + 0.016*"bonus" + 0.013*"imagine"
Topic: 1 Word: 0.016*"energy" + 0.010*"phase" + 0.010*"shake" + 0.010*"crash" + 0.009*"metabolism" + 0.008*"replacement" + 0.008*"product" + 0.007*"elevate" + 0.007*"sustain" + 0.007*"enhance"
Topic: 2 Word: 0.015*"file" + 0.009*"nutrition" + 0.008*"thank" + 0.007*"suggest" + 0.007*"victoria" + 0.007*"regard" + 0.007*"sansom" + 0.007*"5129639748" + 0.007*"victoryburns@yahoo.com" + 0.007*"caraway"
Topic: 3 Word: 0.030*"company" + 0.027*"excite" + 0.022*"nutritional" + 0.019*"200.00" + 0.016*"associate" + 0.011*"every" + 0.011*"inventory" + 0.010*"saturday" + 0.010*"entire" + 0.010*"vemma"
Topic: 4 Word: 0.030*"idnutrition" + 0.020*"need" + 0.018*"nutrient" + 0.017*"assessment" + 0.016*"taking" + 0.015*"nutritional" + 0.015*"health" + 0.012*"pharmaceutical" + 0.011*"grade" + 0.010*"ingest"
Topic: 5 Word

In [16]:
for index, score in sorted(lda_model_success[bow_corpus_success[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_success.print_topic(index, 10)))


Score: 0.6859452128410339	 
Topic: 0.072*"file" + 0.039*"regard" + 0.036*"suggest" + 0.032*"idlife" + 0.029*"video" + 0.015*"product" + 0.014*"dettmer" + 0.014*"jdettmer@hotmail.com" + 0.012*"please" + 0.012*"thanks"

Score: 0.20286984741687775	 
Topic: 0.048*"company" + 0.035*"associate" + 0.033*"excite" + 0.029*"saturday" + 0.025*"every" + 0.024*"april" + 0.021*"idlife" + 0.019*"bonus" + 0.018*"would" + 0.018*"great"

Score: 0.07936162501573563	 
Topic: 0.047*"health" + 0.033*"assessment" + 0.024*"provide" + 0.020*"taking" + 0.020*"need" + 0.018*"idlife" + 0.018*"begin" + 0.013*"recommendation" + 0.013*"nutrition" + 0.013*"please"


In [ ]:
for index, score in sorted(lda_model_tfidf_success[bow_corpus_success[4310]], key=lambda tup: -1*tup[1]):
    print("\nScore: {}\t \nTopic: {}".format(score, lda_model_tfidf.print_topic(index, 10)))

In [27]:
import pyLDAvis
import pyLDAvis.gensim
pyLDAvis.enable_notebook()
pyLDAvis.utils
from pyLDAvis import _prepare

In [19]:
corpus_success = [dictionary.doc2bow(text) for text in success]
extracted_vis_success = pyLDAvis.gensim._extract_data(lda_model_success, corpus_success, dictionary)

In [23]:
corpus_fail = [dictionary.doc2bow(text) for text in failed]
extracted_vis_fail = pyLDAvis.gensim._extract_data(lda_model_fail, corpus_fail, dictionary)

In [28]:
pyLDAvis.enable_notebook()
#extracted = pyLDAvis.gensim._extract_data(lda_model_tfidf, corpus, dictionary)
vis_success = _prepare.prepare(n_jobs=8,**extracted_vis_success)

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [29]:
pyLDAvis.enable_notebook()
#extracted = pyLDAvis.gensim._extract_data(lda_model_tfidf, corpus, dictionary)
vis_fail = _prepare.prepare(n_jobs=8,**extracted_vis_fail)

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [30]:
with open('lda_success.pickle', 'wb') as f:
    pickle.dump(vis_success,f)
with open('lda_fail.pickle', 'wb') as f:
    pickle.dump(vis_fail,f)

In [31]:
pyLDAvis.display(vis_success)

In [32]:
pyLDAvis.display(vis_fail)

In [38]:
extracted_vis_fail_tfidf = pyLDAvis.gensim._extract_data(lda_model_tfidf_fail, corpus_fail, dictionary)
vis_fail_tfidf = _prepare.prepare(n_jobs=8,**extracted_vis_fail_tfidf)

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [39]:
extracted_vis_success_tfidf = pyLDAvis.gensim._extract_data(lda_model_tfidf_success, corpus_success, dictionary)
vis_success_tfidf = _prepare.prepare(n_jobs=8,**extracted_vis_success_tfidf)

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [41]:
pyLDAvis.display(vis_fail_tfidf)

In [40]:
pyLDAvis.display(vis_success_tfidf)

In [42]:
from gensim.models.phrases import Phrases, Phraser
phrases = Phrases(all)

In [43]:
trigrams = Phrases(phrases[all])

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/phrases.py:494: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [48]:
bi_dictionary = gensim.corpora.Dictionary([phrases[msg] for msg in all])
tri_dict = gensim.corpora.Dictionary([trigrams[msg] for msg in all])

In [46]:
bi_dictionary_fail = gensim.corpora.Dictionary([phrases[msg] for msg in failed])
tri_dict_fail = gensim.corpora.Dictionary([trigrams[msg] for msg in failed])

In [50]:
#print("{} -- {}".format(dictionary[10], bi_dictionary[10]))
bow_corpus_success = [bi_dictionary.doc2bow(doc) for doc in [phrases[msg] for msg in success]]
bow_corpus_fail = [bi_dictionary.doc2bow(doc) for doc in [phrases[msg] for msg in failed]]
tfidf_success = models.TfidfModel(bow_corpus_success)
tfidf_failed = models.TfidfModel(bow_corpus_fail)
corpus_tfidf_success = tfidf_success[bow_corpus_success]
corpus_tfidf_failed = tfidf_failed[bow_corpus_fail]


In [55]:
lda_model_tfidf_success = gensim.models.LdaMulticore(corpus_tfidf_success, num_topics=10, id2word=bi_dictionary, passes=2, workers=8)
lda_bi_success = pyLDAvis.gensim.prepare(lda_model_tfidf_success, bow_corpus_success, bi_dictionary)


/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

...

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [57]:
pyLDAvis.display(lda_bi_success)

In [58]:
lda_model_tfidf_fail = gensim.models.LdaMulticore(corpus_tfidf_fail, num_topics=10, id2word=bi_dictionary, passes=2, workers=8)
lda_bi_fail = pyLDAvis.gensim.prepare(lda_model_tfidf_fail, bow_corpus_fail, bi_dictionary)


/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

...

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/anant/anaconda3/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogt

/home/anant/anaconda3/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


In [59]:
pyLDAvis.display(lda_bi_fail) 

In [64]:
with open ('lda_tfidf_bigram_fail.html', 'w') as f:
    pyLDAvis.save_html(lda_bi_fail, f)